**Important: This notebook will only work with fastai-0.7.x. Do not try to run any fastai-1.x code from this path in the repository because it will load fastai-0.7.x**

# NasNet Dogs v Cats

In [ ]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline

In [ ]:
from fastai.conv_learner import *
PATH = "data/dogscats/"
sz=224; bs=48

In [ ]:
def nasnet(pre): return nasnetalarge(pretrained = 'imagenet' if pre else None)
model_features[nasnet]=4032*2

In [ ]:
stats = ([0.5, 0.5, 0.5], [0.5, 0.5, 0.5])
tfms = tfms_from_stats(stats, sz, aug_tfms=transforms_side_on, max_zoom=1.1)
data = ImageClassifierData.from_paths(PATH, tfms=tfms, bs=bs)

In [ ]:
learn = ConvLearner.pretrained(nasnet, data, precompute=True, xtra_fc=[], ps=0.5)

In [ ]:
%time learn.fit(1e-2, 2)

In [ ]:
learn.precompute=False
learn.bn_freeze=True

In [ ]:
%time learn.fit(1e-2, 1, cycle_len=1)

In [ ]:
learn.save('nas_pre')

In [ ]:
def freeze_to(m, n):
    c=children(m[0])
    for l in c:     set_trainable(l, False)
    for l in c[n:]: set_trainable(l, True)

In [ ]:
freeze_to(learn.model, 17)

In [ ]:
learn.fit([1e-5,1e-4,1e-2], 1, cycle_len=1)

In [ ]:
learn.save('nas')